# Mid-Term Assignment

##### Group 4:
1. Piyush Sunil Borse 25PGAI0026
2. Prateek Majumder 25PGAI0027
3. Bhawana Thawarani 25PGAI0137
4. Prajwal Wagh 25PGAI0109
5. Yuvraj Singh Srinet 25PGAI0019

In [0]:
#import some necessary libraries
import re
from pyspark.sql import SparkSession
from datetime import datetime

In [0]:
#reading the csv data using MultiLine=True as it is multi line csv file
tweets = spark.read.options(delimiter=",", header=True, multiLine=True, mode="PERMISSIVE").csv("/FileStore/tables/Sample_tweets_csv.csv")

In [0]:
# Convert to RDD
rdd = tweets.rdd
rdd.take(5)

Out[3]: [Row(user_name='Navaldeep Singh', text='Suresh raina has the best room out of all the players  #IPL2020', user_followers='1311', date='25-08-2020', user_location='Melbourne / New Delhi', source='Twitter for iPhone', user_description='#AppleFan #CricketAddict and a happy husband ☺️'),
 Row(user_name='Naseh Mohtesham', text='All of the Country is So Much into #IPL2020  This Year ...  \nThanks @BCCI .. Best Decision To Host IPL This Year', user_followers='165', date='29-09-2020', user_location=None, source='Twitter for iPhone', user_description='MBA 👨\u200d🎓, Cricket 🏏, Politics 💰, RCB Freak 🥰'),
 Row(user_name='Sports segment', text='#IPL2020 CSK win toss and bowl #IPL #RRvCSK', user_followers='3', date='22-09-2020', user_location=None, source='Twitter Web App', user_description='The official Account of https://t.co/pJmosdM65g'),
 Row(user_name='kamli kudi 🤪', text='Pooran 🔥🔥\nFinally !! 🥳🥳💃💃\n\n#SaddaPunjab\xa0 #IPL2020\xa0 #KXIP\xa0 #RCBvKXIP', user_followers='29', date='15-10-

## 1. Find top 5 hashtag trends for different months

In [0]:
# Extract Relevant hashtags by month with Error Handling for null values
def extract_month_hashtags(row):
    if row['date']:
        try:
            month = datetime.strptime(row['date'], '%d-%m-%Y').strftime('%Y-%m')
            hashtags = [word for word in row['text'].split() if word.startswith('#')]
            return [(month, hashtag) for hashtag in hashtags]  #return the month of the tweet and the hashtag
        except ValueError:
            return []
    else:
        return []

In [0]:
#flatMap to get (month, hashtag) pairs using the flatmap function
month_hashtag_pairs = rdd.flatMap(extract_month_hashtags)
month_hashtag_pairs.take(5)     

Out[5]: [('2020-08', '#IPL2020'),
 ('2020-09', '#IPL2020'),
 ('2020-09', '#IPL2020'),
 ('2020-09', '#IPL'),
 ('2020-09', '#RRvCSK')]

In [0]:
#mapping each (month, hashtag) to ((month, hashtag), 1) so we can get the counts next
month_hashtag_count_pairs = month_hashtag_pairs.map(lambda x: (x, 1))

In [0]:
#reduce by key to get the counts of Hashtag by month
hashtag_counts = month_hashtag_count_pairs.reduceByKey(lambda a, b: a + b)
hashtag_counts.take(10)

Out[7]: [(('2020-08', '#IPL2020'), 985),
 (('2020-09', '#IPL2020'), 13926),
 (('2020-09', '#IPL'), 1123),
 (('2020-09', '#RRvCSK'), 362),
 (('2020-10', '#SaddaPunjab'), 103),
 (('2020-10', '#IPL2020'), 11395),
 (('2020-10', '#KXIP'), 728),
 (('2020-10', '#RCBvKXIP'), 241),
 (('2020-11', '#IPL2020'), 4365),
 (('2020-11', '#IPL2020playoffs'), 23)]

In [0]:
#transform and Group by Month
month_hashtag_counts = hashtag_counts.map(lambda x: (x[0][0], (x[0][1], x[1])))
grouped_by_month = month_hashtag_counts.groupByKey()

In [0]:
#Sort the data and Select Top 5 Hashtags
def top_5_hashtags(iterator):
    sorted_hashtags = sorted(iterator, key=lambda x: x[1], reverse=True)
    return sorted_hashtags[:5]

top_hashtags_by_month = grouped_by_month.mapValues(top_5_hashtags)

In [0]:
top_hashtags_by_month.take(3)

Out[10]: [('2020-08',
  [('#IPL2020', 985),
   ('#IPL', 155),
   ('#Dream11', 104),
   ('#IPLinUAE', 101),
   ('#CSK', 93)]),
 ('2020-09',
  [('#IPL2020', 13926),
   ('#IPL', 1123),
   ('#CSK', 1094),
   ('#Dream11IPL', 1087),
   ('#ipl2020', 1062)]),
 ('2020-10',
  [('#IPL2020', 11395),
   ('#CSK', 1162),
   ('#Dream11IPL', 1074),
   ('#IPL', 787),
   ('#KXIP', 728)])]

In [0]:
#Format the Output to get the appropriate ranks for the hashtags and counts
def format_output(month, hashtags):
    results = []
    for rank, (hashtag, count) in enumerate(hashtags, start=1):
        results.append((month, rank, hashtag, count))
    return results

final_results = top_hashtags_by_month.flatMap(lambda x: format_output(x[0], x[1]))

In [0]:
#show all top 5 for all the months
final_results.take(25)

Out[12]: [('2020-08', 1, '#IPL2020', 985),
 ('2020-08', 2, '#IPL', 155),
 ('2020-08', 3, '#Dream11', 104),
 ('2020-08', 4, '#IPLinUAE', 101),
 ('2020-08', 5, '#CSK', 93),
 ('2020-09', 1, '#IPL2020', 13926),
 ('2020-09', 2, '#IPL', 1123),
 ('2020-09', 3, '#CSK', 1094),
 ('2020-09', 4, '#Dream11IPL', 1087),
 ('2020-09', 5, '#ipl2020', 1062),
 ('2020-10', 1, '#IPL2020', 11395),
 ('2020-10', 2, '#CSK', 1162),
 ('2020-10', 3, '#Dream11IPL', 1074),
 ('2020-10', 4, '#IPL', 787),
 ('2020-10', 5, '#KXIP', 728),
 ('2020-11', 1, '#IPL2020', 4365),
 ('2020-11', 2, '#MI', 495),
 ('2020-11', 3, '#IPLfinal', 476),
 ('2020-11', 4, '#MIvDC', 470),
 ('2020-11', 5, '#MIvsDC', 422)]

Hence, we get the top 5 tweets of all months.

## 2. Find the trends of tweets (number of tweets) for each team over different months.

In [0]:
team_abbreviations = ['CSK', 'MI', 'RCB', 'KKR', 'SRH', 'DC', 'KXIP', 'RR']

In [0]:
#extract the month from the date and identify the team mentioned in the tweet
def extract_month_team(row):
    if row['date'] and row['text']:
        try:
            month = datetime.strptime(row['date'], '%d-%m-%Y').strftime('%Y-%m')
            text = row['text']
            teams = [team for team in team_abbreviations if team in text]
            return [(team, month) for team in teams]  #Return the team and the month
        except ValueError:
            return []
    else:
        return []

#FlatMap to get (team, month) pairs
team_month_pairs = rdd.flatMap(extract_month_team)

In [0]:
team_month_pairs.take(10)

Out[15]: [('CSK', '2020-09'),
 ('RR', '2020-09'),
 ('RCB', '2020-10'),
 ('KXIP', '2020-10'),
 ('DC', '2020-10'),
 ('KXIP', '2020-10'),
 ('KKR', '2020-10'),
 ('DC', '2020-10'),
 ('RCB', '2020-09'),
 ('KXIP', '2020-09')]

In [0]:
#Map all the (team, month) to ((team, month), 1) so that we can reduce by key to get counts
team_month_count_pairs = team_month_pairs.map(lambda x: (x, 1))

#Reduce by key ((team, month)) to sum up counts
team_month_counts = team_month_count_pairs.reduceByKey(lambda a, b: a + b)
team_month_counts.take(10)

Out[16]: [(('CSK', '2020-09'), 3529),
 (('RR', '2020-09'), 2692),
 (('RCB', '2020-10'), 2788),
 (('KXIP', '2020-10'), 2524),
 (('DC', '2020-10'), 2634),
 (('KKR', '2020-10'), 2159),
 (('RCB', '2020-09'), 3954),
 (('KXIP', '2020-09'), 2584),
 (('RR', '2020-10'), 2585),
 (('MI', '2020-09'), 3237)]

In [0]:
def format_output(record):
    team_month, count = record
    team, month = team_month
    return (team, month, count)

#collect the results and format the data
final_results_team_hashtags = team_month_counts.map(format_output)
final_results_team_hashtags.take(10)

Out[17]: [('CSK', '2020-09', 3529),
 ('RR', '2020-09', 2692),
 ('RCB', '2020-10', 2788),
 ('KXIP', '2020-10', 2524),
 ('DC', '2020-10', 2634),
 ('KKR', '2020-10', 2159),
 ('RCB', '2020-09', 3954),
 ('KXIP', '2020-09', 2584),
 ('RR', '2020-10', 2585),
 ('MI', '2020-09', 3237)]

In [0]:
#Group by the team name (first field)
grouped_rdd = final_results_team_hashtags.groupBy(lambda x: x[0])

In [0]:
#Collect and format the results into a rdd
grouped_results = grouped_rdd.flatMap(lambda x:list(x[1]))
grouped_results.take(40)

Out[19]: [('CSK', '2020-09', 3529),
 ('CSK', '2020-10', 3649),
 ('CSK', '2020-08', 195),
 ('CSK', '2020-11', 110),
 ('RR', '2020-09', 2692),
 ('RR', '2020-10', 2585),
 ('RR', '2020-11', 72),
 ('RR', '2020-08', 21),
 ('RCB', '2020-10', 2788),
 ('RCB', '2020-09', 3954),
 ('RCB', '2020-11', 1260),
 ('RCB', '2020-08', 179),
 ('KXIP', '2020-10', 2524),
 ('KXIP', '2020-09', 2584),
 ('KXIP', '2020-11', 39),
 ('KXIP', '2020-08', 29),
 ('DC', '2020-10', 2634),
 ('DC', '2020-09', 1754),
 ('DC', '2020-11', 2005),
 ('DC', '2020-08', 32),
 ('KKR', '2020-10', 2159),
 ('KKR', '2020-09', 2011),
 ('KKR', '2020-11', 172),
 ('KKR', '2020-08', 54),
 ('MI', '2020-09', 3237),
 ('MI', '2020-11', 1893),
 ('MI', '2020-10', 2156),
 ('MI', '2020-08', 53),
 ('SRH', '2020-09', 1892),
 ('SRH', '2020-11', 1556),
 ('SRH', '2020-10', 2353),
 ('SRH', '2020-08', 23)]

In [0]:
#1st 5 records
grouped_results.take(5)

Out[20]: [('CSK', '2020-09', 3529),
 ('CSK', '2020-10', 3649),
 ('CSK', '2020-08', 195),
 ('CSK', '2020-11', 110),
 ('RR', '2020-09', 2692)]

Hence, we get the number of tweets for each team over the months.

## 3. Identify the top 5 tweets for each hashtag, ordered by the number of followers the users have, who have tweeted.

In [0]:
#function to get info about hashtags
def extract_hashtag_info(row):
    if row['text'] and row['user_name'] and row['user_followers']:
        try:
            hashtags = [word for word in row['text'].split() if word.startswith('#')]
            user_name = row['user_name']
            user_followers = int(row['user_followers'])
            tweet = row['text']
            return [(hashtag, (tweet, user_name, user_followers)) for hashtag in hashtags]  #return hashtag, tweet, username and user followers
        except (ValueError, TypeError):
            return []
    else:
        return []

#flatMap to get (hashtag, (tweet, user_name, user_followers)) information on the desired format
hashtag_info_pairs = rdd.flatMap(extract_hashtag_info)

In [0]:
#Group by hashtag : groupbykey
grouped_by_hashtag = hashtag_info_pairs.groupByKey()

In [0]:
#top 5 tweets 
def top_5_tweets(iterator):
    seen_users = set() #checked users
    top_tweets = []
    sorted_tweets = sorted(iterator, key=lambda x: x[2], reverse=True)
    for tweet, user_name, user_followers in sorted_tweets:
        if user_name not in seen_users: #get information for new users
            top_tweets.append((tweet, user_name, user_followers))
            seen_users.add(user_name)
        if len(top_tweets) == 5:
            break
    return top_tweets

top_tweets_by_hashtag = grouped_by_hashtag.mapValues(top_5_tweets)
top_tweets_by_hashtag.take(1) #top 5 tweets for the 1st hashtag

Out[23]: [('#IPL2020',
  [('&amp; a fantastic catch by the athletic Nagarkoti.\n\n@TC59’s 54 towards the end got @rajasthanroyals to a respectable total.\n\n#RRvKKR #IPL2020',
    'Sachin Tendulkar',
    34065868),
   ('Watch | Chennai Super Kings #IPL2020 plans thrown in for a toss after Suresh Raina withdraws and two players test p… https://t.co/kT9SQgG78D',
    'NDTV',
    13595550),
   ('#IPL2020 #SRHvMI #MIvSRH  \n\nWin against @mipaltan has boosted our confidence, says @rashidkhan_19 🏏\n\nWATCH 🧐📹… https://t.co/URcOgtGqsP',
    'The Times Of India',
    13216435),
   ('Faf du Plessis Blessed With A Baby Girl Ahead Of IPL 2020, CSK Shares Pic On Social Media\n#IPL2020 \nhttps://t.co/bZSKo5RlP0',
    'ABP News',
    10332613),
   ('#IPL2020 | #RajasthanRoyals | #RR\n\nRR likely #IPL XI: Does talented Yashasvi Jaiswal fit in Royals’ batting-heavy t… https://t.co/ADZBWDmGrJ',
    'TIMES NOW',
    9824665)])]

In [0]:
#now getting the output in format
# Hashtag, list of 5 tweets, the username who has tweeted and the number of followers
def format_output(record):
    hashtag, tweets_info = record
    result = (hashtag, [{'tweet': tweet, 'user_name': user_name, 'user_followers': user_followers} for tweet, user_name, user_followers in tweets_info])
    return result

#collect the results and format them
final_results_3 = top_tweets_by_hashtag.map(format_output)


In [0]:
#resuls
final_results_3.take(5)

Out[25]: [('#IPL2020',
  [{'tweet': '&amp; a fantastic catch by the athletic Nagarkoti.\n\n@TC59’s 54 towards the end got @rajasthanroyals to a respectable total.\n\n#RRvKKR #IPL2020',
    'user_name': 'Sachin Tendulkar',
    'user_followers': 34065868},
   {'tweet': 'Watch | Chennai Super Kings #IPL2020 plans thrown in for a toss after Suresh Raina withdraws and two players test p… https://t.co/kT9SQgG78D',
    'user_name': 'NDTV',
    'user_followers': 13595550},
   {'tweet': '#IPL2020 #SRHvMI #MIvSRH  \n\nWin against @mipaltan has boosted our confidence, says @rashidkhan_19 🏏\n\nWATCH 🧐📹… https://t.co/URcOgtGqsP',
    'user_name': 'The Times Of India',
    'user_followers': 13216435},
   {'tweet': 'Faf du Plessis Blessed With A Baby Girl Ahead Of IPL 2020, CSK Shares Pic On Social Media\n#IPL2020 \nhttps://t.co/bZSKo5RlP0',
    'user_name': 'ABP News',
    'user_followers': 10332613},
   {'tweet': '#IPL2020 | #RajasthanRoyals | #RR\n\nRR likely #IPL XI: Does talented Yashasvi Jaiswa

Hence, we have got the output in the desired format.

## 4.Create an inverted index of hashtags

In [0]:
def extract_hashtag_info(row):
    if row['date'] and row['text']:
        try:
            month = datetime.strptime(row['date'], '%d-%m-%Y').strftime('%Y-%m')
            hashtags = [word for word in row['text'].split() if word.startswith('#')]
            tweet = row['text']
            return [(hashtag, (month, tweet)) for hashtag in hashtags]  #getting the output in the desired format
        except (ValueError, TypeError):
            return []
    else:
        return []

#FlatMap to get (hashtag, (month, tweet)) pairs so that the output can be formatted next
hashtag_info_pairs = rdd.flatMap(extract_hashtag_info)

In [0]:
hashtag_info_pairs.take(5)

Out[27]: [('#IPL2020',
  ('2020-08',
   'Suresh raina has the best room out of all the players  #IPL2020')),
 ('#IPL2020',
  ('2020-09',
   'All of the Country is So Much into #IPL2020  This Year ...  \nThanks @BCCI .. Best Decision To Host IPL This Year')),
 ('#IPL2020', ('2020-09', '#IPL2020 CSK win toss and bowl #IPL #RRvCSK')),
 ('#IPL', ('2020-09', '#IPL2020 CSK win toss and bowl #IPL #RRvCSK')),
 ('#RRvCSK', ('2020-09', '#IPL2020 CSK win toss and bowl #IPL #RRvCSK'))]

In [0]:
#Map to ((hashtag, month), tweet) pairs
hashtag_month_tweet_pairs = hashtag_info_pairs.map(lambda x: ((x[0], x[1][0]), x[1][1]))

#Group by (hashtag, month)
grouped_by_hashtag_month = hashtag_month_tweet_pairs.groupByKey()


In [0]:
grouped_by_hashtag_month.take(5)

Out[29]: [(('#IPL2020', '2020-08'),
  <pyspark.resultiterable.ResultIterable at 0x7f52482890a0>),
 (('#IPL2020', '2020-09'),
  <pyspark.resultiterable.ResultIterable at 0x7f5248289100>),
 (('#IPL', '2020-09'),
  <pyspark.resultiterable.ResultIterable at 0x7f5248289190>),
 (('#RRvCSK', '2020-09'),
  <pyspark.resultiterable.ResultIterable at 0x7f52482891c0>),
 (('#SaddaPunjab', '2020-10'),
  <pyspark.resultiterable.ResultIterable at 0x7f5248289220>)]

In [0]:
#we can see that we need to format the output

def format_output(record):
    hashtag_month, tweets = record
    hashtag, month = hashtag_month
    tweets_list = list(tweets)
    return (hashtag, month, tweets_list)

# Collect the results and format them
final_results_4 = grouped_by_hashtag_month.map(format_output)



In [0]:
final_results_4.take(5)

Out[31]: [('#IPL2020',
  '2020-08',
  ['Suresh raina has the best room out of all the players  #IPL2020',
   'We miss you @ImRaina , @ChennaiIPL is incomplete without you.\n#ChennaiSuperKings \n#IPL2020 \n#SureshRaina',
   '@ICC It will continue in #IPL2020 💛🦁',
   'Kohli and other RCB Players will reach UAE Tomorrow ✌️\n\n#PlayBold #IPL2020',
   'Crime of hatred n passion r on rise n it must stop now \n#IPL2020 #2YearsofCorruPTIon #covidmillionaires… https://t.co/GZG2duOhVS',
   'Will miss you Mr. IPL ☑️\n\n#IPL #IPL13 #IPL2020 #CSK #ChennaiSuperKings #WhistlePodu #MSDhoni #Dhoni #SureshRaina… https://t.co/rn97dir4P1',
   'BREAKING: Senior CSK All-rounder @ImRaina pulls out of #IPL2020 due to personal problems. Earlier 12 member of CSK… https://t.co/FL2Vu2LYhu',
   'Aakash Chopra is excited before MS Dhoni’s return in IPL 2020. #Cricket #AakashChopra #MSDhoni #IPL2020 #CricTips https://t.co/kvxQLjnUK3',
   'Stop calling it ‘Mankading’. It’s runout. Period  #IPL2020',
   '🤙🏻💥💥Hitman de

Hence, the output is received in the correct format.

In [0]:
results_collected= final_results_4.collect()

### Some other ways to see the output. 

In [0]:
display(results_collected)

_1 _2 _3 #IPL2020 2020-08 List(Suresh raina has the best room out of all the players #IPL2020, We miss you @ImRaina , @ChennaiIPL is incomplete without you.
#ChennaiSuperKings 
#IPL2020 
#SureshRaina, @ICC It will continue in #IPL2020 💛🦁, Kohli and other RCB Players will reach UAE Tomorrow ✌️

#PlayBold #IPL2020, Crime of hatred n passion r on rise n it must stop now 
#IPL2020 #2YearsofCorruPTIon #covidmillionaires… https://t.co/GZG2duOhVS, Will miss you Mr. IPL ☑️

#IPL #IPL13 #IPL2020 #CSK #ChennaiSuperKings #WhistlePodu #MSDhoni #Dhoni #SureshRaina… https://t.co/rn97dir4P1, BREAKING: Senior CSK All-rounder @ImRaina pulls out of #IPL2020 due to personal problems. Earlier 12 member of CSK… https://t.co/FL2Vu2LYhu, Aakash Chopra is excited before MS Dhoni’s return in IPL 2020. #Cricket #AakashChopra #MSDhoni #IPL2020 #CricTips https://t.co/kvxQLjnUK3, Stop calling it ‘Mankading’. It’s runout. Period #IPL2020, 🤙🏻💥💥Hitman deserve it 🤩@ImRo45 
@MIFansClubTN 
@mipaltan 
#RohitSharma 
#Hitman
#IPL2020 
#டீம்MI https://t.co/IGsyiK8Z2S, BCCI Worried For Players' Safety After Coronavirus Cases in UAE Increase Rapidly
#IPLinUAE #IPL2020 #IPL #BCCI… https://t.co/lPPuGT4Woo, #IPL2020 
#IPL2020Updates 
@ImRaina 
@IPL 
@ChennaiIPL 
Bad news fr CSK https://t.co/38Jl8YkXSx, thank you thala @msdhoni
#DhoniRetires 💔
I'll wipe my tears 😭 and get ready for #IPL2020 @ChennaiIPL… https://t.co/cXEvRuZFpT, Really Worried For #IPL2020 Now. 19 Looks Too Far For Me Now. 19 More Days 😭, #BREAKING: Suresh Raina pulls out of IPL due to personal reasons.

https://t.co/2ZXYzRX2xU

#IPL2020 #CSK #SureshRaina, @MalaysiaCricket MCA T20 Super Series 2020 is set to commence from 28th August 2020🏏
#Cricket #IPL2020 #IPL… https://t.co/f6OXT5uRfC, @cricketcontest Hope to win Team
@cricketcontest
#ContestAlert 
#IPL2020 #WinFreePrizes #StayHomeStaySafe… https://t.co/d4gbEkS9Vs, #Tata, #Dream11, #Jio, #Patanjali, #Byju's and #Unacademy show interest for #IPL2020 title sponsorship big question… https://t.co/sGNYDTPouM, Illawarra Premier League: 

A close call for the Rangers

#FSC #SCF #IPL2020 #Illawarra #IPL #Footy #Football… https://t.co/bkntRzqm0T, BCCI is also looking to decrease day games #IPL2020 https://t.co/OgRslWvEib, #IPL2020 title sponsorship rights go to Dream 11 for Rs. 222 crores., Another year has passed but memories are still fresh
#FirstConfessionOut #CPL20 #IPL2020 #ENGvPAK #WCT… https://t.co/d8JuUqlLS9, Many Congratulations @Dream11 for bagging the sponsorship of @IPL this year #Dream11IPL2020 #Dream11 #IPL2020 #IPLinUAE, #CSK vs #MI #IPL2020 Opener on Sep 19th in #UAE https://t.co/1EomKyNYWd, They are going to win IPL 2020 (if it happens) !!! Then they will make a movie on it. #CSK #IPL2020 #IPL2020Updates… https://t.co/qpvaZFBl5P, #Dream11 Reaction After getting Sponsorship of #IPL2020 
#MadeInIndia https://t.co/OnSqmGHdXf, Upcoming months : No work only IPL IPL 💯💯 
#IPL2020, Suresh Raina to miss entire IPL 2020 due to personal reasons
 #IPL2020Updates #IPL2020 #ChennaiSuperKings… https://t.co/KKDuQN7At7, S Badrinath has more IPL Final appearances than these two. #IPL2020 https://t.co/5NiQqUUAAp, Congrats @Dream11 for bagging #IPL2020 title sponsorship https://t.co/qysOa1e7cf, @Dream11 Bags @IPL #2020 #TitleSponsership for 222Crores 👍
#IPL #IPL2020 
#IndianPremierLeague… https://t.co/ScGixVgMxY, Top 5 Innings of @PrithviShaw in IPL Matches.

#PrithviShaw #ipl #IPLt20 #IPL2020 #DC #Sportzcraazy #cricket

https://t.co/Bl9uEfPnNh, #dhoni #Msdian hard to believe but truth is truth
Best of luck for #IPL2020 🔥 #yellove @ChennaiIPL 
@msdhoni, 12 #ChennaiSuperKings support staff and 1 player test positive for #Coronavirus in Dubai. Team goes into quarantine.
#IPL2020, .@CAITIndia has written to Union Minister Shri @KirenRijiju seeking his immediate intervention in the #IPL2020 titl… https://t.co/pKP6KLB41k, Do you know?

#JonnyBairstow #IPL2020 #IPL @IPL @SunRisers https://t.co/gblAeo7Rtv, #IPL2020 #IPLinUAE 

Former @IPL players Sangwan, Suyal to travel

In [0]:
#Print the results
for result in results_collected:
    print(result)

('#IPL2020', '2020-08', ['Suresh raina has the best room out of all the players  #IPL2020', 'We miss you @ImRaina , @ChennaiIPL is incomplete without you.\n#ChennaiSuperKings \n#IPL2020 \n#SureshRaina', '@ICC It will continue in #IPL2020 💛🦁', 'Kohli and other RCB Players will reach UAE Tomorrow ✌️\n\n#PlayBold #IPL2020', 'Crime of hatred n passion r on rise n it must stop now \n#IPL2020 #2YearsofCorruPTIon #covidmillionaires… https://t.co/GZG2duOhVS', 'Will miss you Mr. IPL ☑️\n\n#IPL #IPL13 #IPL2020 #CSK #ChennaiSuperKings #WhistlePodu #MSDhoni #Dhoni #SureshRaina… https://t.co/rn97dir4P1', 'BREAKING: Senior CSK All-rounder @ImRaina pulls out of #IPL2020 due to personal problems. Earlier 12 member of CSK… https://t.co/FL2Vu2LYhu', 'Aakash Chopra is excited before MS Dhoni’s return in IPL 2020. #Cricket #AakashChopra #MSDhoni #IPL2020 #CricTips https://t.co/kvxQLjnUK3', 'Stop calling it ‘Mankading’. It’s runout. Period  #IPL2020', '🤙🏻💥💥Hitman deserve it 🤩@ImRo45  \n@MIFansClubTN \n@mip

## 5. Frequency of sources for each month

This metric will show the count of the source of tweets for each month.

In [0]:
def extract_month_source_info(row):
    if row['date'] and row['source']:
        try:
            month = datetime.strptime(row['date'], '%d-%m-%Y').strftime('%Y-%m')
            source = row['source']
            return (month, source)   #getting the required data
        except (ValueError, TypeError):
            return None
    else:
        return None

#Map to get (month, source) pairs
month_source_pairs = rdd.map(extract_month_source_info).filter(lambda x: x is not None)

In [0]:
# Map to ((month, source), 1) pairs so that they can be reduced next
month_source_count_pairs = month_source_pairs.map(lambda x: ((x[0], x[1]), 1))

In [0]:
#Reduce by key to sum up counts
source_counts_by_month = month_source_count_pairs.reduceByKey(lambda a, b: a + b)
source_counts_by_month.take(5)

Out[37]: [(('2020-08', 'Twitter for iPhone'), 133),
 (('2020-09', 'Twitter for iPhone'), 2471),
 (('2020-09', 'Twitter Web App'), 4278),
 (('2020-10', 'Twitter for iPhone'), 2193),
 (('2020-11', 'Twitter Web App'), 1553)]

In [0]:
#getting the output in a proper format
def format_output(record):
    (month, source), count = record
    return (month, source, count)

#Collect the results and format them
final_results_5 = source_counts_by_month.map(format_output)


In [0]:
final_results_5.take(10)

Out[39]: [('2020-08', 'Twitter for iPhone', 133),
 ('2020-09', 'Twitter for iPhone', 2471),
 ('2020-09', 'Twitter Web App', 4278),
 ('2020-10', 'Twitter for iPhone', 2193),
 ('2020-11', 'Twitter Web App', 1553),
 ('2020-10', 'Twitter Web App', 4507),
 ('2020-10', 'TweetDeck', 1137),
 ('2020-10', 'Twitter for Android', 10360),
 ('2020-09', 'Twitter for Android', 13613),
 ('2020-09', 'CodeVsCode_', 3)]

In [0]:
# Sort by count in descending order
sorted_results = final_results_5.sortBy(lambda x: x[2], ascending=False)

In [0]:
sorted_results.take(10)

Out[41]: [('2020-09', 'Twitter for Android', 13613),
 ('2020-10', 'Twitter for Android', 10360),
 ('2020-10', 'Twitter Web App', 4507),
 ('2020-09', 'Twitter Web App', 4278),
 ('2020-11', 'Twitter for Android', 4012),
 ('2020-09', 'Twitter for iPhone', 2471),
 ('2020-10', 'Twitter for iPhone', 2193),
 ('2020-11', 'Twitter Web App', 1553),
 ('2020-10', 'TweetDeck', 1137),
 ('2020-08', 'Twitter for Android', 1085)]

In [0]:
collected_sorted_results=sorted_results.collect()
# Print the results
for result in collected_sorted_results:
    print(result)

('2020-09', 'Twitter for Android', 13613)
('2020-10', 'Twitter for Android', 10360)
('2020-10', 'Twitter Web App', 4507)
('2020-09', 'Twitter Web App', 4278)
('2020-11', 'Twitter for Android', 4012)
('2020-09', 'Twitter for iPhone', 2471)
('2020-10', 'Twitter for iPhone', 2193)
('2020-11', 'Twitter Web App', 1553)
('2020-10', 'TweetDeck', 1137)
('2020-08', 'Twitter for Android', 1085)
('2020-09', 'TweetDeck', 894)
('2020-11', 'Twitter for iPhone', 883)
('2020-08', 'Twitter Web App', 428)
('2020-11', 'TweetDeck', 383)
('2020-08', 'Twitter for iPhone', 133)
('2020-08', 'TweetDeck', 107)
('2020-10', 'IPLT20 Live', 94)
('2020-09', 'IPLT20 Live', 71)
('2020-10', 'Twitter for iPad', 65)
('2020-10', 'Hootsuite Inc.', 61)
('2020-09', 'Twitter for iPad', 56)
('2020-10', 'Twitter Media Studio', 55)
('2020-09', 'Hootsuite Inc.', 52)
('2020-09', 'Buffer', 49)
('2020-10', 'Buffer', 49)
('2020-09', 'Twitter Media Studio', 40)
('2020-11', 'Hootsuite Inc.', 38)
('2020-10', 'IFTTT', 37)
('2020-08', 'Ho

Hence we have all the sources in a sorted manner.

## 6.Find the Top 10 Users with the Most Tweets for Each Month 

This metric will find the top 10 users with the most tweets every month. We will also return the number of tweets they tweeted.

In [0]:
def extract_month_user_info(row):
    if row['date'] and row['user_name']:
        try:
            month = datetime.strptime(row['date'], '%d-%m-%Y').strftime('%Y-%m')
            user = row['user_name']
            return (month, user)
        except (ValueError, TypeError):
            return None
    else:
        return None

#Map to get (month, user) pairs
month_user_pairs = rdd.map(extract_month_user_info).filter(lambda x: x is not None)

In [0]:
#Map to ((month, user), 1) pairs
month_user_count_pairs = month_user_pairs.map(lambda x: ((x[0], x[1]), 1))

In [0]:
#Reduce by key to sum up counts
user_counts_by_month = month_user_count_pairs.reduceByKey(lambda a, b: a + b)

In [0]:
#Map to (month, (user, count)) pairs
month_user_count_list = user_counts_by_month.map(lambda x: (x[0][0], (x[0][1], x[1])))

#Group by month
grouped_by_month = month_user_count_list.groupByKey()

In [0]:
#Sort by count in descending order and take top 10
def get_top_10_users(record):
    month, user_counts = record
    sorted_user_counts = sorted(user_counts, key=lambda x: x[1], reverse=True)
    top_10_users = sorted_user_counts[:10]
    return (month, top_10_users)

top_10_users_by_month = grouped_by_month.map(get_top_10_users)

In [0]:
#getting the data for the 4 months
top_10_users_by_month.take(4)

Out[48]: [('2020-08',
  [('Yahoo! Cricket', 20),
   ('Circle of Cricket', 19),
   ('Republic', 17),
   ('InsideSport', 16),
   ('Tentaran Sports', 15),
   ('SportsFlashes', 15),
   ('E^2', 14),
   ('TOI Sports', 13),
   ('CricketNDTV', 10),
   ('XtraTime', 10)]),
 ('2020-09',
  [('Yahoo! Cricket', 112),
   ('CricketNDTV', 94),
   ('Circle of Cricket', 75),
   ('IndianPremierLeague', 71),
   ('InsideSport', 70),
   ('SportsTiger', 70),
   ('TOI Sports', 66),
   ('Cricadium CRICKET', 63),
   ('SportsMonks', 59),
   ('Firstpost Sports', 56)]),
 ('2020-10',
  [('Yahoo! Cricket', 142),
   ('CricketNDTV', 140),
   ('SportsTiger', 131),
   ('SportsMonks', 102),
   ('Way2win & Co | Data & Analytics | www.way2win.in', 100),
   ('TOI Sports', 97),
   ('InsideSport', 96),
   ('IndianPremierLeague', 95),
   ('Circle of Cricket', 90),
   ('CricTracker', 83)]),
 ('2020-11',
  [('Yahoo! Cricket', 54),
   ('ESPNcricinfo', 40),
   ('InsideSport', 37),
   ('TOI Sports', 33),
   ('Cricbuzz', 33),
   ('HT

## 7. Get Top Counts of User Locations

We will analyze which locations have had the most users.

In [0]:
def extract_month_location_info(row):
    if row['date'] and row['user_location']:
        try:
            month = datetime.strptime(row['date'], '%d-%m-%Y').strftime('%Y-%m')
            location = row['user_location']
            return (month, location)
        except (ValueError, TypeError):
            return None
    else:
        return None

#Map to get (month, user_location) pairs
month_location_pairs = rdd.map(extract_month_location_info).filter(lambda x: x is not None)

In [0]:
#Map to ((month, user_location), 1) pairs
month_location_count_pairs = month_location_pairs.map(lambda x: ((x[0], x[1]), 1))

In [0]:
#Reduce by key to sum up counts
location_counts_by_month = month_location_count_pairs.reduceByKey(lambda a, b: a + b)

In [0]:
#Map to (month, user_location, count) 
formatted_results = location_counts_by_month.map(lambda x: (x[0][0], x[0][1], x[1]))

#Sort by count in descending order
sorted_results = formatted_results.sortBy(lambda x: x[2], ascending=False)

In [0]:
#top locations
sorted_results.take(15)

Out[53]: [('2020-09', 'India', 2346),
 ('2020-10', 'India', 2049),
 ('2020-09', 'Mumbai, India', 923),
 ('2020-10', 'Mumbai, India', 791),
 ('2020-11', 'India', 699),
 ('2020-09', 'New Delhi, India', 643),
 ('2020-10', 'New Delhi, India', 550),
 ('2020-09', 'Hyderabad, India', 492),
 ('2020-10', 'Hyderabad, India', 337),
 ('2020-11', 'Mumbai, India', 321),
 ('2020-09', 'Bengaluru, India', 310),
 ('2020-09', 'Chennai, India', 298),
 ('2020-10', 'Bengaluru, India', 265),
 ('2020-09', 'Mumbai', 245),
 ('2020-10', 'Chennai, India', 238)]

## 8. Average Number of Hashtags per Tweet for Each User. Find Top users with most Avg hashtags.

Average number of hashtags a user uses in his/her tweet. Also getting the users with the most avg hashtags.

In [0]:
def extract_user_hashtags_info(row):
    if row['user_name'] and row['text']:
        user = row['user_name']
        hashtags = row['text'].split()  # Split text by spaces to get hashtags
        return (user, hashtags)
    else:
        return None

#map to get (user, hashtags) pairs
user_hashtags_pairs = rdd.map(extract_user_hashtags_info).filter(lambda x: x is not None)

In [0]:
#map to (user, count) pairs where count is the number of hashtags in the tweet
user_hashtags_count_pairs = user_hashtags_pairs.map(lambda x: (x[0], len([word for word in x[1] if word.startswith('#')])))

In [0]:
user_hashtags_count_pairs.take(5)

Out[56]: [('Navaldeep Singh', 1),
 ('Naseh Mohtesham', 1),
 ('Sports segment', 3),
 ('kamli kudi 🤪', 4),
 ('Himanshu Dixit', 6)]

In [0]:
#reduce by key to sum up counts
total_hashtags_by_user = user_hashtags_count_pairs.reduceByKey(lambda a, b: a + b)

In [0]:
#now we map to (user, (total hashtags, count of tweets)) pairs
user_total_count_pairs = user_hashtags_pairs.map(lambda x: (x[0], (len(x[1]), 1)))

#next we educe by key to sum up total number of tweets and total number of hashtags
user_total_counts = user_total_count_pairs.reduceByKey(lambda a, b: (a[0] + b[0], a[1] + b[1]))

#join with total_hashtags_by_user to calculate average
user_avg_hashtags = user_total_counts.join(total_hashtags_by_user)\
    .map(lambda x: (x[0], x[1][1] / x[1][0][1]))  # Calculate average hashtags per tweet

#convert to (user, average hashtags) pairs
average_hashtags_per_user = user_avg_hashtags.map(lambda x: (x[0], x[1]))


In [0]:
average_hashtags_per_user.take(10)

Out[59]: [('Navaldeep Singh', 0.6666666666666666),
 ('Naseh Mohtesham', 1.0),
 ('Sports segment', 1.5),
 ('kamli kudi 🤪', 4.0),
 ('Himanshu Dixit', 6.0),
 ('CricTracker', 3.672727272727273),
 ('Wisden India', 1.565217391304348),
 ('Stat Doctor🩺', 0.9333333333333333),
 ('Ankeet Kumar Hanny', 2.0),
 ('Anubhav Sachdeva', 1.0)]

In [0]:
#sort by average hashtags in descending order
sorted_results_average_hashtags_per_user = average_hashtags_per_user.sortBy(lambda x: x[1], ascending=False)

In [0]:
#Top 10 users with most avg hashtags
sorted_results_average_hashtags_per_user.take(10)

Out[61]: [('Sports Arenaa Cricket', 14.0),
 ('#ராக்கிங் #ராம்', 13.0),
 ('Sports Lens', 12.875),
 ('Yuva Yuvi ©', 12.0),
 ('Taarini Dagar', 12.0),
 ('ꪜiᧁꪀꫀડꫝ ᴹᵃˢᵗᵉʳ', 12.0),
 ('Ronaldo Mondal', 12.0),
 ('Shubham Budhwat', 11.5),
 ('GS™ Dada', 11.5),
 ('SaidSo', 11.0)]